In [3]:
import pandas as pd
import numpy as np
import re
import nltk
from nltk.corpus import stopwords
from collections import Counter
import datetime
import pytz

In [707]:
### Load the pickle files to pandas dataframes. 
movie_data_df = pd.read_pickle("movie_data_df.pkl")
actor_data_df = pd.read_pickle("actor_data_df.pkl")
movie_awards_df = pd.read_pickle("movie_awards_df.pkl")
music_awards_df = pd.read_pickle("music_awards_df.pkl")

In [708]:
# Display the heads.
display(movie_data_df.head())
display(movie_data_df.tail())
display(actor_data_df.head())
display(movie_awards_df.head())
display(music_awards_df.head())

imdbID                                           Title  Year Rated  \
0  tt0056952                                  The Cool World  1963  None   
1  tt0065944  King: A Filmed Record... Montgomery to Memphis  1970  None   
2  tt0066559                What Do You Say to a Naked Lady?  1970     X   
3  tt0067741                                           Shaft  1971     R   
4  tt0068358                                 Charley-One-Eye  1973     R   

                    Released Runtime                              Genre  \
0        1964-11-02 00:00:00     105                     [Crime, Drama]   
1  1970-03-24 00:00:00+00:00     185  [Documentary, Biography, History]   
2        1970-02-18 00:00:00      85              [Documentary, Comedy]   
3        1971-07-02 00:00:00     100          [Action, Crime, Thriller]   
4  1973-04-18 00:00:00+00:00      96                          [Western]   

                             Director  \
0                      Shirley Clarke   
1  Sidney Lumet, Joseph L. Mankiewicz   
2                          Allen Funt   
3                        Gordon Parks   
4                         Don Chaffey   

                                              Writer  \
0          [Shirley Clarke, Carl Lee, Warren Miller]   
1                  [Mitchell Grayson, Ely A. Landau]   
2                                       [Allen Funt]   
3  [Ernest Tidyman, John D.F. Black, Ernest Tidyman]   
4                                    [Keith Leonard]   

                                         Lead_Actors  ...  \
0        [Rony Clanton, Carl Lee, Yolanda Rodríguez]  ...   
1  [Paul Newman, Joanne Woodward, Ruby Dee, James...  ...   
2  [Joie Addison, Laura Huston, Martin Meyers, Ka...  ...   
3  [Richard Roundtree, Moses Gunn, Charles Cioffi...  ...   
4  [Richard Roundtree, Roy Thinnes, Nigel Davenpo...  ...   

                                          Movie_Crew  \
0  [Hugh A. Robertson, Robert Rossen, Carl Lee, F...   
1  [Sidney Lumet, Joseph L. Mankiewicz, Richard K...   
2  [Urs Furrer, Steve Karmen, Allen Funt, Tom Man...   
3  [Ernest Tidyman, Isaac Hayes, Gordon Parks, Jo...   
4  [James Swann, John Cameron, Don Chaffey, Tim H...   

                                          Movie_Cast     Budget  \
0  [Rony Clanton, Carl Lee, Yolanda Rodríguez, Cl...        0.0   
1  [Martin Luther King, Coretta Scott King, Ralph...        0.0   
2  [Allen Funt, Joie Addison, Laura Huston, Marti...        0.0   
3  [Richard Roundtree, Moses Gunn, Charles Cioffi...  4000000.0   
4  [Richard Roundtree, Roy Thinnes, Nigel Davenpo...        0.0   

  Opening_Weekend_Gross Worldwide_Gross  \
0                   NaN             NaN   
1                   NaN             NaN   
2                   NaN             NaN   
3                   NaN             NaN   
4                   NaN             NaN   

                                  Soundtrack_Credits alternative_titles Type  \
0                                               None                0.0  NaN   
1                                               None                2.0  NaN   
2                                               None                2.0  NaN   
3  [[nm0005002, Isaac Hayes], [nm0005002, Isaac H...                1.0  NaN   
4                                               None                3.0  NaN   

  Alternative_Titles                                  Supporting_Actors  
0                NaN  [Antonio Fargas, Evadney Canegata, Gary Bollin...  
1                NaN  [Tony Bennett, Leonard Bernstein, Joan Baez, M...  
2                NaN  [Donna Whitfield, Allen Funt, Ernie Monah, Joa...  
3                NaN  [Gwenn Mitchell, Rex Robbins, Victor Arnold, J...  
4                NaN  [Aldo Sambrell, Johnny Sekka, Rafael Albaicín,...  

[5 rows x 31 columns]

imdbID              Title  Year      Rated             Released  \
8182  tt9876426  Love Takes Flight  2019       TV-G  2019-04-27 00:00:00   
8184  tt9883024             Tribes  2020       None  2020-01-23 00:00:00   
8185  tt9887580      Bulletproof 2  2020  Not Rated  2020-01-07 00:00:00   
8186  tt9893250       I Care a Lot  2020          R  2021-02-19 00:00:00   
8187  tt9893846             Zoetic  2019      TV-14  2019-05-03 00:00:00   

     Runtime                    Genre                 Director  \
8182      87                {Romance}         Steven R. Monroe   
8184      11           {Short,Comedy}                Nino Aldi   
8185      97          {Action,Comedy}         Don Michael Paul   
8186     118  {Comedy,Crime,Thriller}               J Blakeson   
8187      16                  {Short}  Wesley Chan, Julie Zhan   

                                         Writer  \
8182                            {"Eric Brooks"}   
8184                           {"Andy Marlatt"}   
8185         {"Don Michael Paul","Rich Wilkes"}   
8186                             {"J Blakeson"}   
8187  {"Wesley Chan","Julie Zhan","Julie Zhan"}   

                                            Lead_Actors  ...  \
8182  {"Nikki Deloach","Jeff Hephner","Barbara Niven...  ...   
8184  {"Aina Dumlao","Jake Hunter","Chas Laughlin","...  ...   
8185             {"Faizon Love","Kirk Fox","Tony Todd"}  ...   
8186  {"Rosamund Pike","Peter Dinklage","Eiza Gonzál...  ...   
8187  {"Doug Burch","Zailee Madrigal","Phil Morris",...  ...   

                                             Movie_Crew  \
8182  [Steven R. Monroe, Eric J. Goldstein, Penny Pe...   
8184  [Nino Aldi, Patricia Chica, DeStorm Power, Jak...   
8185                    [Don Michael Paul, Rich Wilkes]   
8186  [Jeanne McCarthy, Bruce Winant, Robert Simonds...   
8187  [Wesley Chan, Julie Zhan, Benson Quach, Michel...   

                                             Movie_Cast Budget  \
8182  [Nikki DeLoach, Jeff Hephner, Barbara Niven, S...    0.0   
8184  [Galen Howard, Jason Stuart, Aina Dumlao, Pame...    0.0   
8185  [Faizon Love, Kirk Fox, Tony Todd, Cassie Clar...    0.0   
8186  [Rosamund Pike, Peter Dinklage, Eiza González,...    0.0   
8187  [Dawn Yuen, Julie Zhan, Zailee Madrigal, Phil ...    0.0   

     Opening_Weekend_Gross Worldwide_Gross  \
8182                  None            None   
8184                  None            None   
8185                  None            None   
8186                  None         1288436   
8187                  None            None   

                                     Soundtrack_Credits alternative_titles  \
8182  {{nm8211034,Nilu},{nm6212420,"Adrianne Gonzale...                0.0   
8184                                               None                0.0   
8185                                               None                2.0   
8186  {{nm0269885,"Richard Fearless"},{nm0948801,"Jo...               14.0   
8187                                               None                0.0   

       Type                                 Alternative_Titles  \
8182  movie                                                 {}   
8184  movie                                                 {}   
8185  movie      {"A prueba de balas 2","A prueba de balas 2"}   
8186  movie  {"퍼펙트 케어","Tudo pelo vosso bem","Descuida, yo ...   
8187  movie                                                 {}   

                                      Supporting_Actors  
8182  [Brandon Quinn, Skylar Olivia Flanagan, Nikki ...  
8184  [DeStorm Power, Pamela Shaddock, Gregory Albre...  
8185  [Tuks Tad Lungu, Jade Hubner, Faizon Love, Pea...  
8186  [Alicia Witt, Damian Young, Gary Tanguay, Eiza...  
8187  [Phil Morris, Zailee Madrigal, Dawn Yuen, Doug...  

[5 rows x 31 columns]

IMDb_ID  TMDb_ID  Gender   Birthday  \
0  nm1004267   195666       1 1976-02-08   
1  nm2351246   479206       1 1981-08-27   
2  nm4555351  1975743       1 1989-05-11   
3  nm0376200    83976       2 1938-02-01   
4  nm0940851    21356       2 1969-07-25   

                                       Movie_Credits                   actor  
0  {Snowflakes,"Alien: Containment",Blooded,"Shoo...  Sharon Duncan-Brewster  
1  {"A Stone Cold Christmas","Bobbi Kristina","Br...       Demetria McKinney  
2  {"Look Again","The Lovely Rejects","Healing Me...             Lauren Neal  
3  {"For the Love of a Dog","Ghost Fever",Clunker...         Sherman Hemsley  
4  {"After All","The Inheritance","The Temptation...           D.B. Woodside

year_award               winner
0 2005-04-01  Nicollette Sheridan
1 1979-04-01           Brad Davis
2 1964-04-01          Martin Ritt
3 1963-04-01       Janet Margolin
4 2008-04-01       Grey's Anatomy

year_award                                             winner
0 2020-05-19  {"Billie Eilish"}{"Finneas O'Connell"," Rob Ki...
1 2020-05-19  {"Bon Iver"}{"BJ Burton"," Brad Cook"," Chris ...
2 2020-05-19  {"Ariana Grande"}{"Charles Anderson"," Tommy B...
3 2020-05-19  {H.E.R.}{"Rodney  Darkchild  Jerkins"," Joseph...
4 2020-05-19  {Khalid}{"Disclosure "," Denis Kosiak"," Ingma...

In [6]:
### Define the pre-processing functions.
def normalise_list_names(names):
    """Normalise lists of names."""
    if names is not None:
        if type(names) is str:
            names = re.sub("[\{\}\"]", "", names)
            names = names.split(",")
            names = [name.upper() for name in names]
        else:
            names = [name.upper() for name in names]
    return names

def normalise_string_names(names):
    """Normalise names by making all letters uppercase."""
    names = names.upper()
    return names

def clean_soundtrack_credits(st_credits):
    """Remove credit duplicates and imdb_ids."""
    st_credits_final = []
    print(f'START: {st_credits}')
    if st_credits is not None:
        if type(st_credits) is str:
            st_credits = re.sub('[\{\}"]', "", st_credits)
            st_credits = st_credits.split(",")
            st_credits = st_credits[1::2]
            for name in st_credits:
                if name.upper() not in st_credits_final:
                    st_credits_final.append(name.upper())
            print(f'FINISH: {st_credits_final}')
            return st_credits_final
        else:
            for credit in st_credits:
                if credit[1].upper() not in st_credits_final:
                    st_credits_final.append(credit[1].upper()) 
            print(f'FINISH: {st_credits_final}')
            return st_credits_final

def clean_writers(writer_list):
    """Remove any text in brackets from the Writer column."""
    writers = []
    for writer in writer_list:
        writer = re.sub("(\(.+\))", "", writer).strip()
        writers.append(writer)
    return writers

def move_actors(lead_actors, supporting_actors, movie_cast):
    """Ensure each actor lists are consistent by adding/removing certain actors."""
    for actor in lead_actors:
        if (actor is not None) and (actor in supporting_actors):
            supporting_actors.remove(actor)
        if actor not in movie_cast:
            movie_cast.append(actor)
    for actor in supporting_actors:
        if actor not in movie_cast:
            movie_cast.append(actor)

def get_total_movie_awards(names, date):
    """Get the total number of movie/acting awards won amongst a group of individuals before the given date."""
    award_count = 0
    for name in names:
        award_count += len(movie_awards_df[(movie_awards_df["year_award"] < date) & (movie_awards_df["winner"].str.contains(name, na=False, regex=False))])
    return award_count

def get_total_music_awards(names, date):
    """Get the total number of music awards won amongst a group of individuals before the given date."""
    award_count = 0
    if names is not None:
        for name in names: 
            award_count += len(music_awards_df[(music_awards_df["year_award"] < date) & (music_awards_df["winner"].str.contains(name, na=False, regex=False))])
    return award_count

def calculate_black_actor_proportion(actors):
    """Calculate the proportion of Black actors that make up a movie's cast."""
    count = 0
    for name in actors:
        if actor_data_df["actor"].str.contains(name, na=False).any():
            count += 1
    if count != 0:
        proportion = count / len(actors)
        return f'{proportion:.2f}'
    else:
        return 0    

def create_word_freq_list(df_column):
    """Create a sorted word frequency list."""
    plot_words = df_column.sum() # concatenate all plots
    word_counts = plot_words.value_counts() # get word counts
    return word_counts

In [710]:
movie_data_df.reset_index(inplace=True)

In [711]:
# Convert Director names into list of names. 
movie_data_df["Director"] = movie_data_df["Director"].map(lambda x: x.split(",")) 

## Normalise text in relevant columns and dataframes.

In [712]:
movie_data_df["Genre"] = movie_data_df["Genre"].map(lambda x: normalise_list_names(x))

In [713]:
movie_data_df["Director"] = movie_data_df["Director"].map(lambda x: normalise_list_names(x))

In [714]:
movie_data_df["Writer"] = movie_data_df["Writer"].map(lambda x: normalise_list_names(x))

In [716]:
movie_data_df["Lead_Actors"] = movie_data_df["Lead_Actors"].map(lambda x: normalise_list_names(x))

In [717]:
movie_data_df["Supporting_Actors"] = movie_data_df["Supporting_Actors"].map(lambda x: normalise_list_names(x))

In [718]:
movie_data_df["Movie_Cast"] = movie_data_df["Movie_Cast"].map(lambda x: normalise_list_names(x))

In [719]:
movie_data_df["Movie_Crew"] = movie_data_df["Movie_Crew"].map(lambda x: normalise_list_names(x))

In [720]:
actor_data_df["actor"] = actor_data_df["actor"].astype(str).map(lambda x: normalise_string_names(x))

In [721]:
movie_awards_df["winner"] = movie_awards_df["winner"].astype(str).map(lambda x: normalise_string_names(x))

In [722]:
music_awards_df["winner"] = music_awards_df["winner"].astype(str).map(lambda x: normalise_string_names(x))

In [723]:
# Clean and normalise soundtrack_credits column.
movie_data_df["Soundtrack_Credits"] = movie_data_df["Soundtrack_Credits"].map(lambda x: clean_soundtrack_credits(x))

START: None
START: None
START: None
START: [['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes'], ['nm0005002', 'Isaac Hayes']]
FINISH: ['ISAAC HAYES']
START: None
START: [['nm0032300'

In [724]:
# Normalise all datetime objects by making them timezone aware (utc).
music_awards_df["year_award"] = pd.to_datetime(music_awards_df["year_award"], utc=True)
movie_awards_df["year_award"] = pd.to_datetime(movie_awards_df["year_award"], utc=True)
movie_data_df["Released"] = movie_data_df["Released"].apply(lambda d: d.replace(tzinfo=pytz.utc))

In [725]:
# Clean Writer column by removing any text in brackets.
# movie_data_df["Writer"] = movie_data_df["Writer"].apply(lambda x: clean_writers(x))

In [726]:
movie_data_df.dropna(subset=["Lead_Actors"], inplace=True)
movie_data_df[movie_data_df["Lead_Actors"].isna()]

Empty DataFrame
Columns: [index, imdbID, Title, Year, Rated, Released, Runtime, Genre, Director, Writer, Lead_Actors, Plot, Language, Country, Metascore, imdbRating, imdbVotes, rtRating, DVD, BoxOffice, Production, Keyword_List, Movie_Crew, Movie_Cast, Budget, Opening_Weekend_Gross, Worldwide_Gross, Soundtrack_Credits, alternative_titles, Type, Alternative_Titles, Supporting_Actors]
Index: []

[0 rows x 32 columns]

In [727]:
movie_data_df.apply(lambda row: move_actors(row["Lead_Actors"], row["Supporting_Actors"], row["Movie_Cast"]), axis=1)

0       None
1       None
2       None
3       None
4       None
        ... 
8017    None
8018    None
8019    None
8020    None
8021    None
Length: 8016, dtype: object

In [728]:
movie_data_df

index     imdbID                                           Title  Year  \
0         0  tt0056952                                  The Cool World  1963   
1         1  tt0065944  King: A Filmed Record... Montgomery to Memphis  1970   
2         2  tt0066559                What Do You Say to a Naked Lady?  1970   
3         3  tt0067741                                           Shaft  1971   
4         4  tt0068358                                 Charley-One-Eye  1973   
...     ...        ...                                             ...   ...   
8017   8182  tt9876426                               Love Takes Flight  2019   
8018   8184  tt9883024                                          Tribes  2020   
8019   8185  tt9887580                                   Bulletproof 2  2020   
8020   8186  tt9893250                                    I Care a Lot  2020   
8021   8187  tt9893846                                          Zoetic  2019   

          Rated                  Released Runtime  \
0          None 1964-11-02 00:00:00+00:00     105   
1          None 1970-03-24 00:00:00+00:00     185   
2             X 1970-02-18 00:00:00+00:00      85   
3             R 1971-07-02 00:00:00+00:00     100   
4             R 1973-04-18 00:00:00+00:00      96   
...         ...                       ...     ...   
8017       TV-G 2019-04-27 00:00:00+00:00      87   
8018       None 2020-01-23 00:00:00+00:00      11   
8019  Not Rated 2020-01-07 00:00:00+00:00      97   
8020          R 2021-02-19 00:00:00+00:00     118   
8021      TV-14 2019-05-03 00:00:00+00:00      16   

                                  Genre  \
0                        [CRIME, DRAMA]   
1     [DOCUMENTARY, BIOGRAPHY, HISTORY]   
2                 [DOCUMENTARY, COMEDY]   
3             [ACTION, CRIME, THRILLER]   
4                             [WESTERN]   
...                                 ...   
8017                          [ROMANCE]   
8018                    [SHORT, COMEDY]   
8019                   [ACTION, COMEDY]   
8020          [COMEDY, CRIME, THRILLER]   
8021                            [SHORT]   

                                   Director  \
0                          [SHIRLEY CLARKE]   
1     [SIDNEY LUMET,  JOSEPH L. MANKIEWICZ]   
2                              [ALLEN FUNT]   
3                            [GORDON PARKS]   
4                             [DON CHAFFEY]   
...                                     ...   
8017                     [STEVEN R. MONROE]   
8018                            [NINO ALDI]   
8019                     [DON MICHAEL PAUL]   
8020                           [J BLAKESON]   
8021             [WESLEY CHAN,  JULIE ZHAN]   

                                                 Writer  ...  \
0             [SHIRLEY CLARKE, CARL LEE, WARREN MILLER]  ...   
1                     [MITCHELL GRAYSON, ELY A. LANDAU]  ...   
2                                          [ALLEN FUNT]  ...   
3     [ERNEST TIDYMAN, JOHN D.F. BLACK, ERNEST TIDYMAN]  ...   
4                                       [KEITH LEONARD]  ...   
...                                                 ...  ...   
8017                                      [ERIC BROOKS]  ...   
8018                                     [ANDY MARLATT]  ...   
8019                    [DON MICHAEL PAUL, RICH WILKES]  ...   
8020                                       [J BLAKESON]  ...   
8021              [WESLEY CHAN, JULIE ZHAN, JULIE ZHAN]  ...   

                                             Movie_Crew  \
0     [HUGH A. ROBERTSON, ROBERT ROSSEN, CARL LEE, F...   
1     [SIDNEY LUMET, JOSEPH L. MANKIEWICZ, RICHARD K...   
2     [URS FURRER, STEVE KARMEN, ALLEN FUNT, TOM MAN...   
3     [ERNEST TIDYMAN, ISAAC HAYES, GORDON PARKS, JO...   
4     [JAMES SWANN, JOHN CAMERON, DON CHAFFEY, TIM H...   
...                                                 ...   
8017  [STEVEN R. MONROE, ERIC J. GOLDSTEIN, PENNY PE...   
8018  [NINO ALDI, PATRICIA CHICA, DESTORM POWER, JAK...   
8019                    [D

## Add total_awards columns to dataframe

In [730]:
# Add the new total_awards columns to the dataframe.
movie_data_df["Total_Awards_Lead_Actors"] = movie_data_df.apply(lambda row: get_total_movie_awards(row["Lead_Actors"], row["Released"]), axis=1)

In [731]:
movie_data_df["Total_Awards_Lead_Actors"]

0        0
1       10
2        0
3        0
4        1
        ..
8017     0
8018     0
8019     0
8020     3
8021     0
Name: Total_Awards_Lead_Actors, Length: 8016, dtype: int64

In [732]:
movie_data_df["Total_Awards_Supporting_Actors"] = movie_data_df.apply(lambda row: get_total_movie_awards(row["Supporting_Actors"], row["Released"]), axis=1)

In [733]:
movie_data_df["Total_Awards_Supporting_Actors"]

0        0
1       15
2        0
3        0
4        0
        ..
8017     0
8018     0
8019     0
8020     4
8021     0
Name: Total_Awards_Supporting_Actors, Length: 8016, dtype: int64

In [734]:
movie_data_df["Total_Awards_Movie_Cast"] = movie_data_df.apply(lambda row: get_total_movie_awards(row["Movie_Cast"], row["Released"]), axis=1)

In [735]:
movie_data_df["Total_Awards_Movie_Cast"]

0        0
1       25
2        0
3        0
4        1
        ..
8017     0
8018     0
8019     0
8020     7
8021     0
Name: Total_Awards_Movie_Cast, Length: 8016, dtype: int64

In [736]:
movie_data_df["Total_Awards_Director"] = movie_data_df.apply(lambda row: get_total_movie_awards(row["Director"], row["Released"]), axis=1)

In [737]:
movie_data_df["Total_Awards_Director"]

0       0
1       1
2       0
3       0
4       0
       ..
8017    0
8018    0
8019    0
8020    0
8021    0
Name: Total_Awards_Director, Length: 8016, dtype: int64

In [738]:
movie_data_df["Total_Awards_Writer"] = movie_data_df.apply(lambda row: get_total_movie_awards(row["Writer"], row["Released"]), axis=1)

In [750]:
movie_data_df["Total_Awards_Writer"]

array([  2,   0,   1,  16,   3,  27,  24,  25,  26,  28,  31,  10,  14,
         7,   4,   5,   8,  15,  32,  34,  38,  40, 114,  12,   6,  11,
        36], dtype=int64)

In [740]:
movie_data_df["Total_Awards_Movie_Crew"] = movie_data_df.apply(lambda row: get_total_movie_awards(row["Movie_Crew"], row["Released"]), axis=1)

In [753]:
movie_data_df["Total_Awards_Movie_Crew"]

array([  0,   1,   4,   7,   2,  10,   6,  16,   5,  12,  11,  18,   3,
         9,  13,  17,  23,   8,  19,  45,  20,  25, 270,  15,  22,  14,
        21,  29,  31], dtype=int64)

In [747]:
movie_data_df["Total_Awards_Soundtrack_Credits"] = movie_data_df.apply(lambda row: get_total_music_awards(row["Soundtrack_Credits"], row["Released"]), axis=1)

In [762]:
movie_data_df

index     imdbID                                           Title  Year  \
0         0  tt0056952                                  The Cool World  1963   
1         1  tt0065944  King: A Filmed Record... Montgomery to Memphis  1970   
2         2  tt0066559                What Do You Say to a Naked Lady?  1970   
3         3  tt0067741                                           Shaft  1971   
4         4  tt0068358                                 Charley-One-Eye  1973   
...     ...        ...                                             ...   ...   
8017   8182  tt9876426                               Love Takes Flight  2019   
8018   8184  tt9883024                                          Tribes  2020   
8019   8185  tt9887580                                   Bulletproof 2  2020   
8020   8186  tt9893250                                    I Care a Lot  2020   
8021   8187  tt9893846                                          Zoetic  2019   

          Rated                  Released Runtime  \
0          None 1964-11-02 00:00:00+00:00     105   
1          None 1970-03-24 00:00:00+00:00     185   
2             X 1970-02-18 00:00:00+00:00      85   
3             R 1971-07-02 00:00:00+00:00     100   
4             R 1973-04-18 00:00:00+00:00      96   
...         ...                       ...     ...   
8017       TV-G 2019-04-27 00:00:00+00:00      87   
8018       None 2020-01-23 00:00:00+00:00      11   
8019  Not Rated 2020-01-07 00:00:00+00:00      97   
8020          R 2021-02-19 00:00:00+00:00     118   
8021      TV-14 2019-05-03 00:00:00+00:00      16   

                                  Genre  \
0                        [CRIME, DRAMA]   
1     [DOCUMENTARY, BIOGRAPHY, HISTORY]   
2                 [DOCUMENTARY, COMEDY]   
3             [ACTION, CRIME, THRILLER]   
4                             [WESTERN]   
...                                 ...   
8017                          [ROMANCE]   
8018                    [SHORT, COMEDY]   
8019                   [ACTION, COMEDY]   
8020          [COMEDY, CRIME, THRILLER]   
8021                            [SHORT]   

                                   Director  \
0                          [SHIRLEY CLARKE]   
1     [SIDNEY LUMET,  JOSEPH L. MANKIEWICZ]   
2                              [ALLEN FUNT]   
3                            [GORDON PARKS]   
4                             [DON CHAFFEY]   
...                                     ...   
8017                     [STEVEN R. MONROE]   
8018                            [NINO ALDI]   
8019                     [DON MICHAEL PAUL]   
8020                           [J BLAKESON]   
8021             [WESLEY CHAN,  JULIE ZHAN]   

                                                 Writer  ...   Type  \
0             [SHIRLEY CLARKE, CARL LEE, WARREN MILLER]  ...    NaN   
1                     [MITCHELL GRAYSON, ELY A. LANDAU]  ...    NaN   
2                                          [ALLEN FUNT]  ...    NaN   
3     [ERNEST TIDYMAN, JOHN D.F. BLACK, ERNEST TIDYMAN]  ...    NaN   
4                                       [KEITH LEONARD]  ...    NaN   
...                                                 ...  ...    ...   
8017                                      [ERIC BROOKS]  ...  movie   
8018                                     [ANDY MARLATT]  ...  movie   
8019                    [DON MICHAEL PAUL, RICH WILKES]  ...  movie   
8020                                       [J BLAKESON]  ...  movie   
8021              [WESLEY CHAN, JULIE ZHAN, JULIE ZHAN]  ...  movie   

                                     Alternative_Titles  \
0                                                   NaN   
1                                                   NaN   
2                                                   NaN   
3                                                   NaN   
4                                                   NaN   
...                                                 ...   
8017                                                 {}   
8

In [772]:
# Calculate the black actor proportions for each film. 
movie_data_df["Black_Lead_Proportion"] = movie_data_df.apply(lambda row: calculate_black_actor_proportion(row["Lead_Actors"]), axis=1)
movie_data_df["Black_Support_Proportion"] = movie_data_df.apply(lambda row: calculate_black_actor_proportion(row["Supporting_Actors"]), axis=1)
movie_data_df["Black_Cast_Proportion"] = movie_data_df.apply(lambda row: calculate_black_actor_proportion(row["Movie_Cast"]), axis=1)

In [777]:
# Convert new columns types to float. 
movie_data_df["Black_Lead_Proportion"] = movie_data_df["Black_Lead_Proportion"].astype(float)
movie_data_df["Black_Support_Proportion"] = movie_data_df["Black_Support_Proportion"].astype(float)
movie_data_df["Black_Cast_Proportion"] = movie_data_df["Black_Cast_Proportion"].astype(float)

In [780]:
# Checkpoint: Save movie data 
movie_data_df.to_pickle("movie_data_df_1705.pkl")

In [4]:
# Load movie data 
movie_data_df = pd.read_pickle("movie_data_df_1705.pkl")

In [7]:
# Extra changes
movie_data_df["Country"] = movie_data_df["Country"].apply(lambda x: normalise_list_names(x))
movie_data_df["Language"] = movie_data_df["Language"].apply(lambda x: normalise_list_names(x))
movie_data_df["Keyword_List"] = movie_data_df["Keyword_List"].apply(lambda x: normalise_list_names(x))

In [15]:
# Checkpoint: Save movie data 
movie_data_df.to_pickle("movie_data_df_1805.pkl")

In [ ]:
# EARLY ERROR HANDLING...
# Locate the rows where Total_Awards_Lead_Actors + Total_Awards_Supporting_Actors does not equal Total_Awards_Movie_Cast.
inconsistent_rows = movie_data_df[(movie_data_df["Total_Awards_Lead_Actors"] + movie_data_df["Total_Awards_Supporting_Actors"] != movie_data_df["Total_Awards_Movie_Cast"])]
indexes = inconsistent_rows.index

# Iterate through the indexes to further inspect the cause of the inconsistencies.
for index in indexes[:10]:
    print(f'Index: {str(index)}') 
    print("Title:")
    display(inconsistent_rows["Title"][index]) 
    print("Lead Actors:")
    display(inconsistent_rows["Lead_Actors"][index])
    print("Total Awards Lead Actors:")
    display(inconsistent_rows["Total_Awards_Lead_Actors"][index])
    print("Supporting Actors:")
    display(inconsistent_rows["Supporting_Actors"][index])
    print("Total Awards Supporting Actors:")
    display(inconsistent_rows["Total_Awards_Supporting_Actors"][index])
    print("Movie Cast:")
    display(inconsistent_rows["Movie_Cast"][index])
    print("Total Awards Movie Cast:") 
    display(inconsistent_rows["Total_Awards_Movie_Cast"][index])
    print("Next row...")

# Make a note of what needs to be changed.

In [ ]:
len(indexes)

In [ ]:
# Index 1: add 'PAUL NEWMAN' and 'JOANNE WOODWARD' to 'Movie_Cast'
movie_data_df["Movie_Cast"][1].extend(["PAUL NEWMAN", "JOANNE WOODWARD"])

# Index 145: remove 'RAÚL JULIÁ' from 'Supporting_Cast' and add to 'Lead_Actors', add 'RAUL JULIA' to 'Movie_Cast'
movie_data_df["Supporting_Actors"][145].remove("RAÚL JULIÁ")
movie_data_df["Lead_Actors"][145].append("RAÚL JULIÁ")
movie_data_df["Movie_Cast"][145].append("RAUL JULIA")

# Index 281: remove 'ANDY GARCÍA' from 'Supporting_Cast' and add to 'Lead_Actors', add 'ANDY GARCIA' to 'Movie_Cast'
movie_data_df["Supporting_Actors"][281].remove("ANDY GARCÍA")
movie_data_df["Lead_Actors"][281].append("ANDY GARCÍA")
movie_data_df["Movie_Cast"][281].append("ANDY GARCIA")

# Index 896: remove 'ANDY GARCÍA' from 'Supporting_Cast' and add to 'Lead_Actors', add 'ANDY GARCIA' to 'Movie_Cast'
movie_data_df["Supporting_Actors"][896].remove("ANDY GARCÍA")
movie_data_df["Lead_Actors"][896].append("ANDY GARCÍA")
movie_data_df["Movie_Cast"][896].append("ANDY GARCIA")

# Index 942: remove 'MICHAEL WILLIAMS' from 'Lead_Actors'
movie_data_df["Lead_Actors"][942].remove("MICHAEL WILLIAMS")

# Index 966: add 'QUEEN LATIFAH' to 'Movie_Cast'
movie_data_df["Movie_Cast"][966].append("QUEEN LATIFAH")

# Index 1067: 'ANDY GARCÍA' from 'Supporting_Cast' and add to 'Lead_Actors', add 'ANDY GARCIA' to 'Movie_Cast'
movie_data_df["Supporting_Actors"][1067].remove("ANDY GARCÍA")
movie_data_df["Lead_Actors"][1067].append("ANDY GARCÍA")
movie_data_df["Movie_Cast"][1067].append("ANDY GARCIA")

# Index 1093: add 'JON AVNET', 'CAROLE BAYER SAGER' and 'ANDY GARCIA' to 'Movie_Cast', add 'ANDY GARCIA' to 'Supporting_Actors'
movie_data_df["Movie_Cast"][1093].extend(["JON AVNET", "CAROLE BAYER SAGER", "ANDY GARCIA"])
movie_data_df["Supporting_Actors"][1093].append("ANDY GARCIA")

# Index 1096: add 'MATT DAMON' to 'Movie_Cast'
movie_data_df["Movie_Cast"][1096].append("MATT DAMON")

# Index 1156: remove 'GAME' from 'Lead_Actors', add 'JAYCEON TERRELL TAYLOR' to 'Lead_Actors'
movie_data_df["Lead_Actors"][1156].remove("GAME")
movie_data_df["Lead_Actors"][1156].append("JAYCEON TERRELL TAYLOR")

# Index 1160: add 'ANGELA DAVIS' and 'MAHERSHALA ALI' to 'Movie_Cast'
movie_data_df["Movie_Cast"][1160].extend(["ANGELA DAVIS", "MAHERSHALA ALI"])

# Index 1418: add 'DUSTIN LANCE BLACK' and 'DAVID BOIES' to 'Movie_Cast'
movie_data_df["Movie_Cast"][1418].extend(["DUSTIN LANCE BLACK", "DAVID BOIES"])

# Index 1442: add 'IDRIS ELBA' to 'Movie_Cast'
movie_data_df["Movie_Cast"][1442].append("IDRIS ELBA")

# Index 1570: add 'MARK RUFFALO' to 'Movie_Cast'
movie_data_df["Movie_Cast"][1570].append("MARK RUFFALO")

# Index 1577: add 'AARON PAUL', 'AASIF MANDVI', 'ADAM LAMBERT' to 'Movie_Cast'
movie_data_df["Movie_Cast"][1577].extend(["AARON PAUL", "AASIF MANDVI", "ADAM LAMBERT"])

# Index 1634: add 'UZO ADUBA', 'LILY ALDRIDGE', 'ABIGAIL ANDERSON' to 'Movie_Cast'
movie_data_df["Movie_Cast"][1634].extend(["UZO ADUBA", "LILY ALDRIDGE", "ABIGAIL ANDERSON"])

# Index 1646: add 'THE BEATLES' to 'Movie_Cast'
movie_data_df["Movie_Cast"][1646].append("THE BEATLES")

# Index 1661: add 'JEFF DANIELS' to 'Movie_Cast'
movie_data_df["Movie_Cast"][1661].append("JEFF DANIELS")

# Index 1702: add 'JOEY LAUREN ADAMS', 'BEN AFFLECK', 'FRED ARMISEN', 'DIEDRICH BADER' to 'Movie_Cast'
movie_data_df["Movie_Cast"][1702].extend(["JOEY LAUREN ADAMS", "BEN AFFLECK", "FRED ARMISEN", "DIEDRICH BADER"])

In [13]:
# Update the total_awards columns.
movie_data_df["Total_Awards_Lead_Actors"] = movie_data_df.apply(lambda row: get_total_movie_awards(row["Lead_Actors"], row["Released"]), axis=1)
movie_data_df["Total_Awards_Supporting_Actors"] = movie_data_df.apply(lambda row: get_total_movie_awards(row["Supporting_Actors"], row["Released"]), axis=1)
movie_data_df["Total_Awards_Movie_Cast"] = movie_data_df.apply(lambda row: get_total_movie_awards(row["Movie_Cast"], row["Released"]), axis=1)
movie_data_df["Total_Awards_Director"] = movie_data_df.apply(lambda row: get_total_movie_awards(row["Director"], row["Released"]), axis=1)
movie_data_df["Total_Awards_Writer"] = movie_data_df.apply(lambda row: get_total_movie_awards(row["Writer"], row["Released"]), axis=1)
movie_data_df["Total_Awards_Movie_Crew"] = movie_data_df.apply(lambda row: get_total_movie_awards(row["Movie_Crew"], row["Released"]), axis=1)
movie_data_df["Total_Awards_Soundtrack_Credits"] = movie_data_df.apply(lambda row: get_total_music_awards(row["Soundtrack_Credits"], row["Released"]), axis=1)

In [ ]:
# Check inconsistencies again.
movie_data_df[(movie_data_df["Total_Awards_Lead_Actors"] + movie_data_df["Total_Awards_Supporting_Actors"] != movie_data_df["Total_Awards_Movie_Cast"])]